### Thesis ADS: Rosa Lucassen

# Loading the data

In [1]:
import pickle
import pandas as pd
import numpy as np
from numpy import array

import spacy
import stop_words
nlp = spacy.load("en_core_web_sm")
nlp.vocab["covid"].is_stop = True
nlp.vocab["corona"].is_stop = True
nlp.vocab["covid19"].is_stop = True
nlp.vocab["covid-19"].is_stop = True
nlp.vocab["coronavirus"].is_stop = True

import re
import emoji
from collections import Counter
from scipy.stats import chi2_contingency
from urllib.parse import urlparse
from nltk.stem.porter import PorterStemmer

import gensim
from gensim.models import Phrases
from gensim.corpora import Dictionary
from gensim.models.wrappers import LdaMallet
from gensim.models.coherencemodel import CoherenceModel
from gensim.models.ldamodel import LdaModel
from gensim.corpora.dictionary import Dictionary

import logging
import pyLDAvis.gensim
import json

import warnings
warnings.filterwarnings('ignore')  # To ignore all warnings that arise here to enhance clarity
stemmer = PorterStemmer()

# Function: Cleaning data

In [2]:
def remove_single_char(text):
    single_char_pattern = r'\s+[a-zA-Z]\s+'
    without_sc = re.sub(pattern=single_char_pattern, repl=" ", string=text)
    return without_sc

def remove_numbers(text):
    number_pattern = r'\b(?<![0-9-])(\d+)(?![0-9-])'
    without_number = re.sub(pattern=number_pattern, repl=" ", string=text)
    return without_number


def remove_urls(text):
    url_pattern = r'https?://\S+|www\.\S+'
    without_urls = re.sub(pattern=url_pattern, repl=" ", string=text)
    return without_urls

def remove_nonalpha(text):
    nonalpha_pattern = "[+$@#?~]"
    without_nonalpha = re.sub(pattern=nonalpha_pattern, repl=" ", string=text)
    return without_nonalpha
    
def remove_rt(text):
    rt_pattern = 'rt @[\w_]+: '
    without_pattern = re.sub(pattern = rt_pattern, repl=" ", string = text)
    return without_pattern 

def remove_extra_spaces(text):
    space_pattern = r'\s+'
    without_space = re.sub(pattern=space_pattern, repl=" ", string=text)
    return without_space

def strip_list_noempty(mylist):
    newlist = (item.strip() if hasattr(item, 'strip') else item for item in mylist)
    return [item for item in newlist if item != '']

# Function: BiGrams

In [3]:
from gensim.models import Phrases
def make_n_grams(docs):
    # Add bigrams and trigrams to docs (only ones that appear 20 times or more).
    bigram = Phrases(docs, min_count=1)
    for idx in range(len(docs)):
        for token in bigram[docs[idx]]:
            if '_' in token:
                # Token is a bigram, add to document.
                docs[idx].append(token)
    return docs

# Function: Lemmatizing texts

In [4]:
def pre_processer(corpus):
    corpus = [remove_urls(text) for text in corpus]
    corpus = [remove_single_char(text) for text in corpus]
    corpus = [remove_numbers(text) for text in corpus]
    corpus = [remove_rt(text) for text in corpus]
    corpus = [remove_nonalpha(text) for text in corpus]
    corpus = [text.encode("ascii", "ignore") for text in corpus]
    corpus = [text.decode() for text in corpus]
    
    my_doc = [nlp(text) for text in corpus]
    
    token_list = []
    for token in my_doc:
        token_list.append(token.text)

    # Create list of word tokens after removing stopwords
    filtered_posts = []
    for post in token_list:
        words = post.split()
        post_new = ""
        for word in words:
            if nlp.vocab[word].is_stop == False:
                post_new += " " + word
        filtered_posts.append(post_new)
    filtered_posts = [remove_extra_spaces(text) for text in filtered_posts]
    filtered_posts = strip_list_noempty(filtered_posts)
    processed_texts = [text for text in nlp.pipe(filtered_posts, 
                                              disable=["ner",
                                                       "parser"])]
    tokenized_texts = [[word.lemma_ for word in lemma_ if not word.is_punct if not word.is_stop] 
                            for lemma_ in processed_texts]
    tokenized_texts = make_n_grams(tokenized_texts)
    
    return filtered_posts, tokenized_texts

# Function: Topic modelling LDA Gensim

In [5]:
# Shows all words instead of just the 10 most popular words
def topic_modelling_results(tokenized_text, n_topics, n_iterations):
    results = []

    dictionary = Dictionary(tokenized_text) # get the vocabulary
    corpus = [dictionary.doc2bow(text) for text in tokenized_text]

    PATH_TO_MALLET = '/Users/rosalucassen/Documents/UU/DataMining/mallet-2.0.8/bin/mallet'
    N_TOPICS = n_topics
    N_ITERATIONS = n_iterations

    lda = LdaMallet(PATH_TO_MALLET,
                    corpus=corpus,
                    id2word=dictionary,
                    num_topics=N_TOPICS,
                    iterations=N_ITERATIONS)
    
    for topic in range(N_TOPICS):
        words = lda.show_topic(topic)
        topic_n_words = ' '.join([word[0] for word in words])
        result = {'Topic':str(topic), 
                    'Words':topic_n_words}
        results.append(result)
    results_DF = pd.DataFrame(results)
    pd.set_option('display.max_colwidth', None)
    return results_DF, lda, dictionary, corpus

# Function: Compute Coherence Scores

In [7]:
def compute_coherence_values(texts, start, step, limit, topn):
    dictionary = Dictionary(texts) # get the vocabulary
    dictionary.filter_extremes(no_below=5, no_above=0.5)
    corpus = [dictionary.doc2bow(text) for text in texts]

    PATH_TO_MALLET = '/Users/rosalucassen/Documents/UU/DataMining/mallet-2.0.8/bin/mallet'
    
    coherence_values = []
    model_list = []
    for num_topics in range(start, limit, step):
        model = gensim.models.wrappers.LdaMallet(PATH_TO_MALLET, corpus=corpus, num_topics=num_topics, id2word=dictionary, alpha=0.1, iterations = 400)
        model_list.append(model)
        coherencemodel = CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v', topn=topn)
        coherence_values.append(coherencemodel.get_coherence())

    return model_list, coherence_values

## Exploring the data

In [8]:
d_test = pd.read_excel("/Users/rosalucassen/Desktop/Thesis/Code/Data/Constraint_English_Test2.xlsx", engine='openpyxl')
d_train = pd.read_excel("/Users/rosalucassen/Desktop/Thesis/Code/Data/Constraint_English_Train.xlsx", engine='openpyxl')
d_val = pd.read_excel("/Users/rosalucassen/Desktop/Thesis/Code/Data/Constraint_English_Val.xlsx", engine='openpyxl')
d_test_labeled = pd.read_excel("/Users/rosalucassen/Desktop/Thesis/Code/Data/english_test_with_labels.xlsx", engine='openpyxl')

#### Combine data

In [9]:
data_train = pd.concat([d_train, d_test_labeled, d_val])
data_train.head()

id                                              tweet label
0   1  The CDC currently reports 99031 deaths. In gen...  real
1   2  States reported 1121 deaths a small rise from ...  real
2   3  Politically Correct Woman (Almost) Uses Pandem...  fake
3   4  #IndiaFightsCorona: We have 1524 #COVID testin...  real
4   5  Populous states can generate large case counts...  real

In [9]:
data_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10700 entries, 0 to 2139
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   id      10700 non-null  int64 
 1   tweet   10700 non-null  object
 2   label   10700 non-null  object
dtypes: int64(1), object(2)
memory usage: 334.4+ KB


In [10]:
grouped_train = data_train.groupby('label').count() 
grouped_train.head()

id  tweet
label             
fake   5100   5100
real   5600   5600

# Pre-processing emotion detection data

In [10]:
corpus_fake = data_train[data_train.label == "fake"]["tweet"]
corpus_real = data_train[data_train.label == "real"]["tweet"]
#corpus = data_train["tweet"]
corpus_fake, tokenized_texts_fake = pre_processer(corpus_fake)
print(corpus_fake)
corpus_real, tokenized_texts_real = pre_processer(corpus_real)
print(corpus_real)
#corpus = pre_processer_fake(corpus)

['Politically Correct Woman (Almost) Uses Pandemic Excuse Reuse Plastic Bag nashville', 'Obama Calls Trumps Coronavirus Response Chaotic Disaster', 'Clearly, Obama administration leave kind game plan like this.', 'RetractionHydroxychloroquine chloroquine macrolide treatment COVID-19: multinational registry analysis - Lancet', 'NBA poised restart month. March reported Utah Jazz got tests matter hours time U.S. testing sluggish.', "Donald Trump's negligence incompetence: - , people died - nearly million cases COVID-19 - million Americans work hes patting back. Unbelievable.", 'Multiple Facebook posts claim Aussies fined found talking conspiracies [COVID-19]. posts included screenshot segment Australian breakfast television evidence claim.', 'Nobel Prize laureate Tasuku Honjo didn\'t "not natural" post Facebook claims. fact Professor Honjo said he\'s "greatly saddened" spread misinformation. latest CoronaCheck:', 'BREAKING NEWS president Cryill Ramaphosa asked foreign nations depart south

['CDC currently reports deaths. general discrepancies death counts different sources small explicable. death toll stands roughly people today.', 'States reported deaths small rise Tuesday. Southern states reported deaths.', 'IndiaFightsCorona: COVID testing laboratories India th August tests : ProfBhargava DG ICMRDELHI StaySafe IndiaWillWin', 'Populous states generate large case counts look new cases million today smaller states showing cases million California Texas: AL AR ID KS KY LA MS NV SC.', 'Covid Act found "on average person Illinois COVID-19 infecting . people. Data shows infection growth rate declined time factors stay-at-home order restrictions place."', 'tested positive COVID19 symptoms stay home away people. Learn CDCs recommendations COVID-19 infection:', 'simple daily precautions help prevent spread respiratory illnesses like COVID19. Learn protect (COVID-19):', 'announced participants age cohort dosed Phase study mRNA vaccine (mRNA-1273) novel coronavirus. Read more: mR

In [11]:
count = 0
for tweet in corpus_fake:
    if (sum(len(i) for i in tweet) < 200):
        count += 1
print(count)

4843


In [12]:
count = 0
for tweet in corpus_real:
    if (sum(len(i) for i in tweet) < 200):
        count += 1
print(count)

5067


## Results: Topic modelling LDA Gensim

#### Fake news

In [11]:
topics, lda_fake, dictionary, corpus_f = topic_modelling_results(tokenized_texts_fake, 8, n_iterations = 1000)
topics

Topic  \
0     0   
1     1   
2     2   
3     3   
4     4   
5     5   
6     6   
7     7   

                                                                            Words  
0                    claim video show post time China Facebook man share lockdown  
1          people government home NEWS Gates number Bill lockdown Bill_Gates stay  
2  pandemic Coronavirus covid-19 health medium social donaldtrump fact check news  
3                          virus mask spread wear day work amp stop message covid  
4            COVID-19 die patient doctor hospital covid-19 Italy year treat image  
5                vaccine death COVID19 COVID world start treatment call find good  
6          COVID-19 test cure positive kill Covid-19 rate water flu test_positive  
7            case Trump India President country state Donald report infection day

#### Real news

In [13]:
topics_real, lda_real, dictionary, corpus_r = topic_modelling_results(tokenized_texts_real, 27, n_iterations = 1000)
topics_real

Topic  \
0      0   
1      1   
2      2   
3      3   
4      4   
5      5   
6      6   
7      7   
8      8   
9      9   
10    10   
11    11   
12    12   
13    13   
14    14   
15    15   
16    16   
17    17   
18    18   
19    19   
20    20   
21    21   
22    22   
23    23   
24    24   
25    25   
26    26   

                                                                                                                  Words  
0                                                       case time April pm death state continue discharge confirm March  
1                                     test positive testing result negative state big antibody cumulative positive_rate  
2           RT PIB_India drharshvardhan RT_PIB_India issue PMOIndia Health RT_drharshvardhan AshwiniKChoubey ddnewslive  
3                                 number test total complete yesterday bring date laboratory test_complete total_number  
4                                case total active active_case confirm_case Health confirm COVID-19 number total_number  
5                                                  people COVID-19 hospital person infection care today group North ICU  
6      case death confirm COVID19Nigeria discharge case_COVID19Nigeria discharged discharged_death discharge_death Akwa  
7                                                high recovery rate India low covid19 record day indiafightscorona Rate  
8                                    case confirm COVID19 confirm_case States total state COVID19_Nigeria Total Nigeria  
9                                       amp lab COVID19 Nigeria covid19 capacity support Lagos State TakeResponsibility  
10                                                      report death today day York low New_York weekend source include  
11                                     health amp symptom public home COVID19 public_health transmission emergency life  
12                                   country vaccine COVID19 DrTedros pandemic amp access ensure DrTedros_COVID19 COVAX  
13  IndiaFightsCorona India lakh StaySafe IndiaWillWin hour MoHFW_INDIA indiafightscorona conduct StaySafe_IndiaWillWin  
14                                                          spread face mask wear stay protect hand slow prevent social  
15                                       state report daily test update state_report track publish million daily_update  
16                                                           COVID19 learn RT covid19 child CDC find visit plan CDCMMWR  
17                COVID19 COVID covid19 COVID_19 CoronavirusIndia today MoHFW_INDIA coronavirusupdate covidupdate trial  
18                      COVID-19 isolation facility manage community update manage_isolation Zealand New_Zealand remain  
19                                            Coronavirus UK restriction government late live lockdown read England add  
20                            day test testing covid19 sample recover September sample_test StaySafe coronavirusupdates  
21                                                       risk patient high virus study long disease severe find illness  
22                                     number state hospitalization outbreak rise record large current begin California  
23                                           datum state important alexismadrigal good change reporting data level work  
24                                                        week increase show continue late CDC COVID South decline U.S.  
25                                  contact people include close Auckland cluster test_positive link community positive  
26                                                       amp work early measure lead worker follow school staff service

## Document topic distribution

###### Loop over documents to get topic distribution: Fake

In [12]:
transformed_docs = lda_fake.load_document_topics()

In [13]:
for i, document in enumerate(transformed_docs):
    print('Topic distributions for document {}'.format(i))
    for topic in document:
        print(topic)

Topic distributions for document 0
(0, 0.13749999999999998)
(1, 0.1208333333333333)
(2, 0.15416666666666665)
(3, 0.10416666666666664)
(4, 0.13749999999999998)
(5, 0.1208333333333333)
(6, 0.1208333333333333)
(7, 0.10416666666666664)
Topic distributions for document 1
(0, 0.10775862068965517)
(1, 0.125)
(2, 0.14224137931034483)
(3, 0.15948275862068967)
(4, 0.125)
(5, 0.125)
(6, 0.10775862068965517)
(7, 0.10775862068965517)
Topic distributions for document 2
(0, 0.12083333333333335)
(1, 0.13750000000000004)
(2, 0.13750000000000004)
(3, 0.10416666666666669)
(4, 0.10416666666666669)
(5, 0.18750000000000003)
(6, 0.10416666666666669)
(7, 0.10416666666666669)
Topic distributions for document 3
(0, 0.11693548387096774)
(1, 0.11693548387096774)
(2, 0.10080645161290322)
(3, 0.11693548387096774)
(4, 0.14919354838709678)
(5, 0.16532258064516128)
(6, 0.10080645161290322)
(7, 0.13306451612903225)
Topic distributions for document 4
(0, 0.125)
(1, 0.0946969696969697)
(2, 0.125)
(3, 0.10984848484848485)

(2, 0.11885245901639344)
(3, 0.10245901639344263)
(4, 0.11885245901639344)
(5, 0.10245901639344263)
(6, 0.15163934426229508)
(7, 0.20081967213114754)
Topic distributions for document 212
(0, 0.13942307692307693)
(1, 0.1201923076923077)
(2, 0.1201923076923077)
(3, 0.1201923076923077)
(4, 0.1201923076923077)
(5, 0.13942307692307693)
(6, 0.1201923076923077)
(7, 0.1201923076923077)
Topic distributions for document 213
(0, 0.15416666666666667)
(1, 0.12083333333333333)
(2, 0.10416666666666667)
(3, 0.10416666666666667)
(4, 0.10416666666666667)
(5, 0.1375)
(6, 0.10416666666666667)
(7, 0.17083333333333334)
Topic distributions for document 214
(0, 0.1267123287671233)
(1, 0.1267123287671233)
(2, 0.09931506849315068)
(3, 0.1404109589041096)
(4, 0.11301369863013698)
(5, 0.09931506849315068)
(6, 0.08561643835616438)
(7, 0.2089041095890411)
Topic distributions for document 215
(0, 0.11885245901639346)
(1, 0.16803278688524592)
(2, 0.1352459016393443)
(3, 0.11885245901639346)
(4, 0.11885245901639346)
(

Topic distributions for document 378
(0, 0.09765625)
(1, 0.11328125)
(2, 0.16015625)
(3, 0.20703125)
(4, 0.11328125)
(5, 0.11328125)
(6, 0.09765625)
(7, 0.09765625)
Topic distributions for document 379
(0, 0.11328125)
(1, 0.12890625)
(2, 0.09765625)
(3, 0.09765625)
(4, 0.16015625)
(5, 0.09765625)
(6, 0.11328125)
(7, 0.19140625)
Topic distributions for document 380
(0, 0.10593220338983052)
(1, 0.17372881355932207)
(2, 0.12288135593220341)
(3, 0.10593220338983052)
(4, 0.10593220338983052)
(5, 0.12288135593220341)
(6, 0.12288135593220341)
(7, 0.1398305084745763)
Topic distributions for document 381
(0, 0.14473684210526316)
(1, 0.12719298245614036)
(2, 0.12719298245614036)
(3, 0.10964912280701754)
(4, 0.10964912280701754)
(5, 0.12719298245614036)
(6, 0.14473684210526316)
(7, 0.10964912280701754)
Topic distributions for document 382
(0, 0.1059322033898305)
(1, 0.17372881355932204)
(2, 0.13983050847457626)
(3, 0.1228813559322034)
(4, 0.1228813559322034)
(5, 0.1059322033898305)
(6, 0.12288135

(0, 0.125)
(1, 0.10775862068965517)
(2, 0.125)
(3, 0.10775862068965517)
(4, 0.14224137931034483)
(5, 0.125)
(6, 0.14224137931034483)
(7, 0.125)
Topic distributions for document 601
(0, 0.09920634920634921)
(1, 0.14682539682539686)
(2, 0.09920634920634921)
(3, 0.09920634920634921)
(4, 0.130952380952381)
(5, 0.19444444444444448)
(6, 0.09920634920634921)
(7, 0.130952380952381)
Topic distributions for document 602
(0, 0.09191176470588237)
(1, 0.18014705882352944)
(2, 0.16544117647058826)
(3, 0.09191176470588237)
(4, 0.10661764705882354)
(5, 0.1360294117647059)
(6, 0.12132352941176472)
(7, 0.10661764705882354)
Topic distributions for document 603
(0, 0.10775862068965517)
(1, 0.15948275862068967)
(2, 0.125)
(3, 0.10775862068965517)
(4, 0.10775862068965517)
(5, 0.14224137931034483)
(6, 0.10775862068965517)
(7, 0.14224137931034483)
Topic distributions for document 604
(0, 0.10080645161290322)
(1, 0.1814516129032258)
(2, 0.1975806451612903)
(3, 0.10080645161290322)
(4, 0.11693548387096774)
(5, 

(2, 0.14436619718309862)
(3, 0.10211267605633806)
(4, 0.21478873239436624)
(5, 0.08802816901408451)
(6, 0.1302816901408451)
(7, 0.11619718309859157)
Topic distributions for document 823
(0, 0.11153846153846152)
(1, 0.09615384615384613)
(2, 0.15769230769230766)
(3, 0.11153846153846152)
(4, 0.09615384615384613)
(5, 0.14230769230769227)
(6, 0.11153846153846152)
(7, 0.17307692307692304)
Topic distributions for document 824
(0, 0.11328125)
(1, 0.14453125)
(2, 0.19140625)
(3, 0.09765625)
(4, 0.09765625)
(5, 0.09765625)
(6, 0.11328125)
(7, 0.14453125)
Topic distributions for document 825
(0, 0.113013698630137)
(1, 0.0993150684931507)
(2, 0.113013698630137)
(3, 0.19520547945205483)
(4, 0.15410958904109592)
(5, 0.0993150684931507)
(6, 0.12671232876712332)
(7, 0.0993150684931507)
Topic distributions for document 826
(0, 0.09191176470588237)
(1, 0.1360294117647059)
(2, 0.09191176470588237)
(3, 0.09191176470588237)
(4, 0.1360294117647059)
(5, 0.19485294117647062)
(6, 0.1360294117647059)
(7, 0.1213

...

(6, 0.13805970149253732)
(7, 0.10820895522388059)
Topic distributions for document 4266
(0, 0.14919354838709678)
(1, 0.10080645161290322)
(2, 0.14919354838709678)
(3, 0.13306451612903225)
(4, 0.16532258064516128)
(5, 0.10080645161290322)
(6, 0.10080645161290322)
(7, 0.10080645161290322)
Topic distributions for document 4267
(0, 0.1318181818181818)
(1, 0.11363636363636363)
(2, 0.11363636363636363)
(3, 0.11363636363636363)
(4, 0.16818181818181818)
(5, 0.1318181818181818)
(6, 0.11363636363636363)
(7, 0.11363636363636363)
Topic distributions for document 4268
(0, 0.13425925925925927)
(1, 0.11574074074074074)
(2, 0.13425925925925927)
(3, 0.11574074074074074)
(4, 0.11574074074074074)
(5, 0.13425925925925927)
(6, 0.13425925925925927)
(7, 0.11574074074074074)
Topic distributions for document 4269
(0, 0.11574074074074076)
(1, 0.11574074074074076)
(2, 0.11574074074074076)
(3, 0.1342592592592593)
(4, 0.17129629629629634)
(5, 0.11574074074074076)
(6, 0.11574074074074076)
(7, 0.11574074074074076)
T

Topic distributions for document 4488
(0, 0.1059322033898305)
(1, 0.1059322033898305)
(2, 0.1228813559322034)
(3, 0.13983050847457626)
(4, 0.1228813559322034)
(5, 0.1228813559322034)
(6, 0.17372881355932204)
(7, 0.1059322033898305)
Topic distributions for document 4489
(0, 0.1228813559322034)
(1, 0.1059322033898305)
(2, 0.1059322033898305)
(3, 0.1059322033898305)
(4, 0.1059322033898305)
(5, 0.1059322033898305)
(6, 0.2076271186440678)
(7, 0.13983050847457626)
Topic distributions for document 4490
(0, 0.15163934426229506)
(1, 0.1024590163934426)
(2, 0.11885245901639341)
(3, 0.1024590163934426)
(4, 0.2172131147540983)
(5, 0.1024590163934426)
(6, 0.1024590163934426)
(7, 0.1024590163934426)
Topic distributions for document 4491
(0, 0.12083333333333335)
(1, 0.12083333333333335)
(2, 0.13750000000000004)
(3, 0.1541666666666667)
(4, 0.1541666666666667)
(5, 0.10416666666666669)
(6, 0.10416666666666669)
(7, 0.10416666666666669)
Topic distributions for document 4492
(0, 0.10775862068965517)
(1, 0.

(1, 0.13851351351351351)
(2, 0.11148648648648649)
(3, 0.08445945945945946)
(4, 0.125)
(5, 0.125)
(6, 0.125)
(7, 0.20608108108108109)
Topic distributions for document 4673
(0, 0.10964912280701754)
(1, 0.12719298245614036)
(2, 0.10964912280701754)
(3, 0.10964912280701754)
(4, 0.10964912280701754)
(5, 0.12719298245614036)
(6, 0.17982456140350878)
(7, 0.12719298245614036)
Topic distributions for document 4674
(0, 0.10661764705882353)
(1, 0.1213235294117647)
(2, 0.15073529411764705)
(3, 0.09191176470588236)
(4, 0.09191176470588236)
(5, 0.15073529411764705)
(6, 0.13602941176470587)
(7, 0.15073529411764705)
Topic distributions for document 4675
(0, 0.115625)
(1, 0.140625)
(2, 0.103125)
(3, 0.078125)
(4, 0.128125)
(5, 0.128125)
(6, 0.203125)
(7, 0.103125)
Topic distributions for document 4676
(0, 0.09920634920634921)
(1, 0.11507936507936509)
(2, 0.09920634920634921)
(3, 0.11507936507936509)
(4, 0.11507936507936509)
(5, 0.16269841269841273)
(6, 0.09920634920634921)
(7, 0.19444444444444448)
Topi

(6, 0.10775862068965518)
(7, 0.10775862068965518)
Topic distributions for document 4877
(0, 0.1516393442622951)
(1, 0.1352459016393443)
(2, 0.10245901639344264)
(3, 0.11885245901639345)
(4, 0.11885245901639345)
(5, 0.11885245901639345)
(6, 0.1352459016393443)
(7, 0.11885245901639345)
Topic distributions for document 4878
(0, 0.14015151515151514)
(1, 0.10984848484848485)
(2, 0.0946969696969697)
(3, 0.0946969696969697)
(4, 0.2765151515151515)
(5, 0.0946969696969697)
(6, 0.0946969696969697)
(7, 0.0946969696969697)
Topic distributions for document 4879
(0, 0.1228813559322034)
(1, 0.1228813559322034)
(2, 0.1228813559322034)
(3, 0.17372881355932204)
(4, 0.1228813559322034)
(5, 0.1228813559322034)
(6, 0.1059322033898305)
(7, 0.1059322033898305)
Topic distributions for document 4880
(0, 0.0992063492063492)
(1, 0.13095238095238096)
(2, 0.17857142857142858)
(3, 0.14682539682539683)
(4, 0.13095238095238096)
(5, 0.0992063492063492)
(6, 0.11507936507936507)
(7, 0.0992063492063492)
Topic distributio

(7, 0.10080645161290322)
Topic distributions for document 5099
(0, 0.1318181818181818)
(1, 0.1318181818181818)
(2, 0.1318181818181818)
(3, 0.11363636363636363)
(4, 0.1318181818181818)
(5, 0.1318181818181818)
(6, 0.11363636363636363)
(7, 0.11363636363636363)


In [14]:
lda_corpus = [max(prob,key=lambda y:y[1]) for prob in lda_fake[corpus_f] ]
playlists = [[] for i in range(8)]
for i, x in enumerate(lda_corpus):
    playlists[x[0]].append(corpus_fake[i])

In [17]:
playlists[1]

['BREAKING NEWS president Cryill Ramaphosa asked foreign nations depart south Africa june increasing cases COVID .',
 'George Soros people responsible new born laboratory.',
 'article claiming "Bill Gates\' vaccine" modify human DNA.',
 'person Galicia / / .',
 'Camila Pitanga Brazilian actress contracted COVID-19 said caught malaria chloroquine admitting wrong.',
 "Bill Gates profits vaccination wants reduce world's population.",
 'Indore India Police doctors injecting positive blood Muslims.',
 'Indian politician Uddhav Thackeray asked Christians pray Jesus stop COVID-19.',
 '"States like New York, Illinois California vocal demands funding bail pension systems, failing long COVID-19 outbreak, programs aren t related crisis."',
 'Trumps effort blame Obama sluggish testing.',
 'Coronavirus spread bananas',
 'Covid19 NYC people saw this, stay home.HORRIBLE. StayHome StayAtHome StaySafe NYC NYCLockdown FridayFeeling',
 'puts facemask skin, gets lockdown &gt;&gt;&gt;',
 'Simpsons predicte

In [15]:
transformed_docs = lda_fake.load_document_topics()
topic_distributions_fake = pd.DataFrame([[x[1] for x in doc] for doc in transformed_docs], 
             columns=['topic_{}'.format(i) for i in range(8)])
topic_distributions_fake.tail()
topic_distributions_fake.mean().sort_values(ascending=False)

topic_7    0.125586
topic_4    0.125574
topic_0    0.125395
topic_2    0.125382
topic_6    0.124854
topic_3    0.124627
topic_1    0.124529
topic_5    0.124053
dtype: float64

In [27]:
count = 0
for i in range(8):
    count += len(playlists[i])
print(count)

5100


###### Loop over documents to get topic distribution: Real

In [32]:
transformed_docs = lda_real.load_document_topics()
for i, document in enumerate(transformed_docs):
    print('Topic distributions for document {}'.format(i))
    for topic in document:
        print(topic)
        
lda_corpus = [max(prob,key=lambda y:y[1]) for prob in lda_real[corpus_r]]
playlists_real = [[] for i in range(27)]
for i, x in enumerate(lda_corpus):
    playlists_real[x[0]].append(corpus_real[i])

Topic distributions for document 0
(0, 0.02723311546840959)
(1, 0.02723311546840959)
(2, 0.02723311546840959)
(3, 0.02723311546840959)
(4, 0.04193899782135077)
(5, 0.07135076252723313)
(6, 0.04193899782135077)
(7, 0.02723311546840959)
(8, 0.05664488017429195)
(9, 0.02723311546840959)
(10, 0.02723311546840959)
(11, 0.02723311546840959)
(12, 0.02723311546840959)
(13, 0.02723311546840959)
(14, 0.02723311546840959)
(15, 0.04193899782135077)
(16, 0.04193899782135077)
(17, 0.02723311546840959)
(18, 0.11546840958605666)
(19, 0.02723311546840959)
(20, 0.02723311546840959)
(21, 0.02723311546840959)
(22, 0.02723311546840959)
(23, 0.04193899782135077)
(24, 0.02723311546840959)
(25, 0.04193899782135077)
(26, 0.04193899782135077)
Topic distributions for document 1
(0, 0.02986857825567504)
(1, 0.02986857825567504)
(2, 0.02986857825567504)
(3, 0.0782556750298686)
(4, 0.02986857825567504)
(5, 0.09438470728793312)
(6, 0.02986857825567504)
(7, 0.02986857825567504)
(8, 0.02986857825567504)
(9, 0.02986857

(25, 0.04938271604938273)
(26, 0.02374169040835708)
Topic distributions for document 73
(0, 0.026455026455026443)
(1, 0.026455026455026443)
(2, 0.04074074074074072)
(3, 0.026455026455026443)
(4, 0.026455026455026443)
(5, 0.026455026455026443)
(6, 0.04074074074074072)
(7, 0.1264550264550264)
(8, 0.026455026455026443)
(9, 0.026455026455026443)
(10, 0.06931216931216928)
(11, 0.04074074074074072)
(12, 0.026455026455026443)
(13, 0.026455026455026443)
(14, 0.026455026455026443)
(15, 0.026455026455026443)
(16, 0.055026455026455)
(17, 0.06931216931216928)
(18, 0.026455026455026443)
(19, 0.026455026455026443)
(20, 0.026455026455026443)
(21, 0.04074074074074072)
(22, 0.026455026455026443)
(23, 0.026455026455026443)
(24, 0.04074074074074072)
(25, 0.026455026455026443)
(26, 0.026455026455026443)
Topic distributions for document 74
(0, 0.03906646372399797)
(1, 0.02536783358701166)
(2, 0.03906646372399797)
(3, 0.02536783358701166)
(4, 0.02536783358701166)
(5, 0.02536783358701166)
(6, 0.0390664637239

(12, 0.02893518518518518)
(13, 0.02893518518518518)
(14, 0.02893518518518518)
(15, 0.02893518518518518)
(16, 0.02893518518518518)
(17, 0.02893518518518518)
(18, 0.02893518518518518)
(19, 0.13831018518518515)
(20, 0.02893518518518518)
(21, 0.04456018518518518)
(22, 0.02893518518518518)
(23, 0.07581018518518517)
(24, 0.02893518518518518)
(25, 0.04456018518518518)
(26, 0.04456018518518518)
Topic distributions for document 127
(0, 0.026838432635534086)
(1, 0.026838432635534086)
(2, 0.026838432635534086)
(3, 0.273215244229737)
(4, 0.026838432635534086)
(5, 0.026838432635534086)
(6, 0.026838432635534086)
(7, 0.026838432635534086)
(8, 0.026838432635534086)
(9, 0.026838432635534086)
(10, 0.026838432635534086)
(11, 0.026838432635534086)
(12, 0.026838432635534086)
(13, 0.041331186258722494)
(14, 0.026838432635534086)
(15, 0.026838432635534086)
(16, 0.026838432635534086)
(17, 0.026838432635534086)
(18, 0.026838432635534086)
(19, 0.026838432635534086)
(20, 0.026838432635534086)
(21, 0.026838432635

(0, 0.030358227079538575)
(1, 0.07953855494839107)
(2, 0.04675166970248941)
(3, 0.030358227079538575)
(4, 0.04675166970248941)
(5, 0.04675166970248941)
(6, 0.030358227079538575)
(7, 0.030358227079538575)
(8, 0.030358227079538575)
(9, 0.030358227079538575)
(10, 0.06314511232544023)
(11, 0.030358227079538575)
(12, 0.030358227079538575)
(13, 0.030358227079538575)
(14, 0.030358227079538575)
(15, 0.04675166970248941)
(16, 0.030358227079538575)
(17, 0.030358227079538575)
(18, 0.030358227079538575)
(19, 0.030358227079538575)
(20, 0.030358227079538575)
(21, 0.04675166970248941)
(22, 0.030358227079538575)
(23, 0.030358227079538575)
(24, 0.04675166970248941)
(25, 0.030358227079538575)
(26, 0.030358227079538575)
Topic distributions for document 181
(0, 0.02608242044861763)
(1, 0.040166927490871154)
(2, 0.02608242044861763)
(3, 0.02608242044861763)
(4, 0.040166927490871154)
(5, 0.040166927490871154)
(6, 0.05425143453312468)
(7, 0.02608242044861763)
(8, 0.02608242044861763)
(9, 0.02608242044861763)

(15, 0.05425143453312468)
(16, 0.02608242044861763)
(17, 0.0683359415753782)
(18, 0.02608242044861763)
(19, 0.02608242044861763)
(20, 0.02608242044861763)
(21, 0.02608242044861763)
(22, 0.02608242044861763)
(23, 0.02608242044861763)
(24, 0.02608242044861763)
(25, 0.05425143453312468)
(26, 0.02608242044861763)
Topic distributions for document 234
(0, 0.02436647173489278)
(1, 0.02436647173489278)
(2, 0.03752436647173489)
(3, 0.02436647173489278)
(4, 0.02436647173489278)
(5, 0.02436647173489278)
(6, 0.02436647173489278)
(7, 0.02436647173489278)
(8, 0.03752436647173489)
(9, 0.03752436647173489)
(10, 0.02436647173489278)
(11, 0.02436647173489278)
(12, 0.02436647173489278)
(13, 0.02436647173489278)
(14, 0.02436647173489278)
(15, 0.02436647173489278)
(16, 0.02436647173489278)
(17, 0.02436647173489278)
(18, 0.2612085769980506)
(19, 0.02436647173489278)
(20, 0.03752436647173489)
(21, 0.02436647173489278)
(22, 0.02436647173489278)
(23, 0.06384015594541909)
(24, 0.02436647173489278)
(25, 0.037524

...

Topic distributions for document 5347
(0, 0.029394473838918293)
(1, 0.029394473838918293)
(2, 0.04526748971193417)
(3, 0.029394473838918293)
(4, 0.029394473838918293)
(5, 0.029394473838918293)
(6, 0.029394473838918293)
(7, 0.04526748971193417)
(8, 0.04526748971193417)
(9, 0.06114050558495005)
(10, 0.029394473838918293)
(11, 0.029394473838918293)
(12, 0.029394473838918293)
(13, 0.029394473838918293)
(14, 0.029394473838918293)
(15, 0.029394473838918293)
(16, 0.04526748971193417)
(17, 0.029394473838918293)
(18, 0.029394473838918293)
(19, 0.06114050558495005)
(20, 0.029394473838918293)
(21, 0.04526748971193417)
(22, 0.029394473838918293)
(23, 0.029394473838918293)
(24, 0.06114050558495005)
(25, 0.029394473838918293)
(26, 0.06114050558495005)
Topic distributions for document 5348
(0, 0.023741690408357084)
(1, 0.16476733143399816)
(2, 0.03656220322886991)
(3, 0.03656220322886991)
(4, 0.06220322886989556)
(5, 0.06220322886989556)
(6, 0.023741690408357084)
(7, 0.03656220322886991)
(8, 0.023741

(17, 0.04256495301271422)
(18, 0.05749032614704259)
(19, 0.027639579878385858)
(20, 0.027639579878385858)
(21, 0.027639579878385858)
(22, 0.027639579878385858)
(23, 0.04256495301271422)
(24, 0.027639579878385858)
(25, 0.027639579878385858)
(26, 0.027639579878385858)
Topic distributions for document 5411
(0, 0.13439599937490232)
(1, 0.0331301765900922)
(2, 0.06688545085169557)
(3, 0.012033130176590093)
(4, 0.02469135802469136)
(5, 0.012033130176590093)
(6, 0.0331301765900922)
(7, 0.020471948741990938)
(8, 0.012033130176590093)
(9, 0.016252539459290515)
(10, 0.02469135802469136)
(11, 0.00781372089388967)
(12, 0.00781372089388967)
(13, 0.00781372089388967)
(14, 0.00781372089388967)
(15, 0.016252539459290515)
(16, 0.071104860134396)
(17, 0.020471948741990938)
(18, 0.00781372089388967)
(19, 0.06688545085169557)
(20, 0.012033130176590093)
(21, 0.11751836224410064)
(22, 0.020471948741990938)
(23, 0.02469135802469136)
(24, 0.12173777152680106)
(25, 0.05844663228629473)
(26, 0.04156899515549304

Topic distributions for document 5471
(0, 0.047530864197530845)
(1, 0.030864197530864185)
(2, 0.030864197530864185)
(3, 0.047530864197530845)
(4, 0.030864197530864185)
(5, 0.047530864197530845)
(6, 0.030864197530864185)
(7, 0.030864197530864185)
(8, 0.030864197530864185)
(9, 0.030864197530864185)
(10, 0.030864197530864185)
(11, 0.030864197530864185)
(12, 0.030864197530864185)
(13, 0.030864197530864185)
(14, 0.030864197530864185)
(15, 0.030864197530864185)
(16, 0.030864197530864185)
(17, 0.030864197530864185)
(18, 0.030864197530864185)
(19, 0.047530864197530845)
(20, 0.030864197530864185)
(21, 0.030864197530864185)
(22, 0.09753086419753082)
(23, 0.030864197530864185)
(24, 0.030864197530864185)
(25, 0.030864197530864185)
(26, 0.06419753086419751)
Topic distributions for document 5472
(0, 0.023441162681669032)
(1, 0.023441162681669032)
(2, 0.023441162681669032)
(3, 0.03609939052977031)
(4, 0.35255508673230224)
(5, 0.023441162681669032)
(6, 0.023441162681669032)
(7, 0.023441162681669032)
(

(16, 0.02763957987838585)
(17, 0.02763957987838585)
(18, 0.057490326147042574)
(19, 0.042564953012714214)
(20, 0.02763957987838585)
(21, 0.02763957987838585)
(22, 0.042564953012714214)
(23, 0.042564953012714214)
(24, 0.02763957987838585)
(25, 0.057490326147042574)
(26, 0.0873410724156993)
Topic distributions for document 5536
(0, 0.028490028490028494)
(1, 0.04387464387464388)
(2, 0.028490028490028494)
(3, 0.05925925925925927)
(4, 0.028490028490028494)
(5, 0.028490028490028494)
(6, 0.028490028490028494)
(7, 0.028490028490028494)
(8, 0.028490028490028494)
(9, 0.028490028490028494)
(10, 0.05925925925925927)
(11, 0.028490028490028494)
(12, 0.04387464387464388)
(13, 0.04387464387464388)
(14, 0.028490028490028494)
(15, 0.04387464387464388)
(16, 0.10541310541310543)
(17, 0.028490028490028494)
(18, 0.028490028490028494)
(19, 0.028490028490028494)
(20, 0.028490028490028494)
(21, 0.04387464387464388)
(22, 0.028490028490028494)
(23, 0.028490028490028494)
(24, 0.028490028490028494)
(25, 0.02849002

(2, 0.02314814814814815)
(3, 0.02314814814814815)
(4, 0.04814814814814816)
(5, 0.02314814814814815)
(6, 0.02314814814814815)
(7, 0.02314814814814815)
(8, 0.02314814814814815)
(9, 0.02314814814814815)
(10, 0.03564814814814816)
(11, 0.07314814814814817)
(12, 0.02314814814814815)
(13, 0.060648148148148166)
(14, 0.03564814814814816)
(15, 0.03564814814814816)
(16, 0.03564814814814816)
(17, 0.02314814814814815)
(18, 0.02314814814814815)
(19, 0.02314814814814815)
(20, 0.03564814814814816)
(21, 0.02314814814814815)
(22, 0.02314814814814815)
(23, 0.2106481481481482)
(24, 0.03564814814814816)
(25, 0.02314814814814815)
(26, 0.02314814814814815)
Topic distributions for document 5597
(0, 0.029868578255675036)
(1, 0.07825567502986859)
(2, 0.029868578255675036)
(3, 0.029868578255675036)
(4, 0.029868578255675036)
(5, 0.04599761051373956)
(6, 0.06212664277180408)
(7, 0.029868578255675036)
(8, 0.029868578255675036)
(9, 0.04599761051373956)
(10, 0.029868578255675036)
(11, 0.029868578255675036)
(12, 0.094

In [33]:
count = 0
for i in range(27):
    count += len(playlists_real[i])
print(count)

5600


In [101]:
transformed_docs = lda_real.load_document_topics()
topic_distributions_real = pd.DataFrame([[x[1] for x in doc] for doc in transformed_docs], 
             columns=['topic_{}'.format(i) for i in range(27)])
topic_distributions_real.tail()
topic_distributions_real.mean().sort_values(ascending=False)

topic_3     0.042825
topic_4     0.042771
topic_9     0.041676
topic_16    0.041601
topic_10    0.041561
topic_5     0.041045
topic_19    0.040365
topic_22    0.040339
topic_14    0.040319
topic_11    0.040177
topic_7     0.039967
topic_2     0.039790
topic_13    0.039737
topic_20    0.039648
topic_0     0.039393
topic_15    0.039371
topic_17    0.039073
topic_8     0.039051
topic_23    0.038970
topic_21    0.038929
topic_1     0.038830
topic_24    0.038768
topic_18    0.038680
topic_6     0.038670
topic_12    0.038445
dtype: float64

## VADER Sentiment Analysis

In [102]:
import nltk
nltk.download('vader_lexicon')
from nltk.sentiment.vader import SentimentIntensityAnalyzer
sid = SentimentIntensityAnalyzer()

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     /Users/rosalucassen/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


#### Real News

In [ ]:
df_real = pd.DataFrame(corpus_real)
df_real.columns = ["Tweet"]
df_real

In [ ]:
df_real['scores'] = df_real['Tweet'].apply(lambda tweet: sid.polarity_scores(tweet))
df_real.head()

In [ ]:
df_real['compound']  = df_real['scores'].apply(lambda score_dict: score_dict['compound'])
df_real.head()

In [ ]:
# Create a function that returns desired values
# You only need to check upper bound as the next elif-statement will catch the value
def func(compound):
    if compound < -0.1:
        return "neg"
    elif compound > 0.1:
        return "pos"
    else:
        return 'neu'
df_real['Class'] = df_real['compound'].apply(func)
df_real.head()

In [ ]:
df_real["compound"].mean()

In [ ]:
df_real['compound'].plot(kind = 'hist')

#### Fake News

In [109]:
def compound_func(compound):
    if compound < -0.1:
        return "neg"
    elif compound > 0.1:
        return "pos"
    else:
        return 'neu'

def VADER(playlists):
    df = pd.DataFrame(playlists)
    df.columns = ["Tweet"]
    df['scores'] = df['Tweet'].apply(lambda tweet: sid.polarity_scores(tweet))
    df['compound']  = df['scores'].apply(lambda score_dict: score_dict['compound'])
    df['Class'] = df['compound'].apply(compound_func)
    return df

In [110]:
df_topic1_fake = VADER(playlists[0])
df_topic2_fake = VADER(playlists[1])
df_topic3_fake = VADER(playlists[2])
df_topic4_fake = VADER(playlists[3])

In [111]:
df_topic1_real = VADER(playlists_real[0])
df_topic2_real = VADER(playlists_real[1])
df_topic3_real = VADER(playlists_real[2])
df_topic4_real = VADER(playlists_real[3])
df_topic5_real = VADER(playlists_real[4])
df_topic6_real = VADER(playlists_real[5])
df_topic7_real = VADER(playlists_real[6])
df_topic8_real = VADER(playlists_real[7])
df_topic9_real = VADER(playlists_real[8])
df_topic10_real = VADER(playlists_real[9])
df_topic11_real = VADER(playlists_real[10])
df_topic12_real = VADER(playlists_real[11])
df_topic13_real = VADER(playlists_real[12])
df_topic14_real = VADER(playlists_real[13])
df_topic15_real = VADER(playlists_real[14])
df_topic16_real = VADER(playlists_real[15])
df_topic17_real = VADER(playlists_real[16])
df_topic18_real = VADER(playlists_real[17])
df_topic19_real = VADER(playlists_real[18])
df_topic20_real = VADER(playlists_real[19])
df_topic21_real = VADER(playlists_real[20])
df_topic22_real = VADER(playlists_real[21])
df_topic23_real = VADER(playlists_real[22])
df_topic24_real = VADER(playlists_real[23])
df_topic25_real = VADER(playlists_real[24])

Tweet  \
0                                                                                                                     government come pressure lack availability tests. Read here:   
1                                                                                               James_Gross reporting effectively. It's refuse numbers table dashboard reasons me.   
2             important work data collection analysis : pm day data Team collates results received testing laboratories inform Nigerians number Results received time reported day   
3                                                        CoronaVirusUpdates: testing status update: ICMRDELHI stated samples upto September sample September StaySafe IndiaWillWin   
4                                                                   RT imperialcollege: UK government announced . million support Prof Robin Shattocks roboskis teams phase trials   
..                                                                                                                                                                             ...   
160                                                                        Avoid Cs. certain places spreads easily: Crowded places Close-contact settings Confined enclosed spaces   
161                                                            CoronaVirusUpdates: testing status update: ICMRDELHI stated samples upto August sample August StaySafe IndiaWillWin   
162                                       important continues play safe. person charge social gathering ensure records kept contact tracing purposes person gathering knows other.   
163  model TheLancet studied contact tracing data people UK. researchers found combining contact tracing quarantining better contained compared mass testing self-isolation alone.   
164                                                      CoronaVirusUpdates: testing status update: ICMRDELHI stated samples upto September sample September StaySafe IndiaWillWin   

                                                             scores  compound  \
0     {'neg': 0.429, 'neu': 0.571, 'pos': 0.0, 'compound': -0.5423}   -0.5423   
1    {'neg': 0.168, 'neu': 0.611, 'pos': 0.221, 'compound': 0.1779}    0.1779   
2      {'neg': 0.0, 'neu': 0.866, 'pos': 0.134, 'compound': 0.2732}    0.2732   
3             {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}    0.0000   
4      {'neg': 0.0, 'neu': 0.828, 'pos': 0.172, 'compound': 0.4019}    0.4019   
..                                                              ...       ...   
160  {'neg': 0.132, 'neu': 0.599, 'pos': 0.269, 'compound': 0.3182}    0.3182   
161           {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}    0.0000   
162    {'neg': 0.0, 'neu': 0.591, 'pos': 0.409, 'compound': 0.8271}    0.8271   
163  {'neg': 0.084, 'neu': 0.795, 'pos': 0.121, 'compound': 0.2263}    0.2263   
164           {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}    0.0000   

    Class  
0     neg  
1     pos  
2     pos  
3     neu  
4     pos  
..    ...  
160   pos  
161   neu  
162   pos  
163   pos  
164   neu  

[165 rows x 4 columns]

In [ ]:
df_fake["compound"].mean()

In [ ]:
df_fake['compound'].plot(kind = 'hist')

#### All News

In [ ]:
df = pd.DataFrame(corpus)
df.columns = ["Tweet"]
df

In [ ]:
df['scores'] = df['Tweet'].apply(lambda tweet: sid.polarity_scores(tweet))
df.head()

In [ ]:
df['compound']  = df['scores'].apply(lambda score_dict: score_dict['compound'])
df.head()

In [ ]:
# Create a function that returns desired values
# You only need to check upper bound as the next elif-statement will catch the value
def func(compound):
    if compound < -0.1:
        return "neg"
    elif compound > 0.1:
        return "pos"
    else:
        return 'neu'
df['Class'] = df['compound'].apply(func)
df.head()

In [ ]:
df["compound"].mean()

In [ ]:
df['compound'].plot(kind = 'hist')

## LIWC Sentiment Analysis

#### Fake news

In [ ]:
def pre_processer_LIWC(corpus):
    corpus = [text.lower() for text in corpus]
    corpus = [remove_urls(text) for text in corpus]
    corpus = [remove_single_char(text) for text in corpus]
    corpus = [remove_numbers(text) for text in corpus]
    corpus = [remove_rt(text) for text in corpus]
    corpus = [remove_emojis(text) for text in corpus]
    corpus = [remove_nonalpha(text) for text in corpus]
    corpus = [text.encode("ascii", "ignore") for text in corpus]
    corpus = [text.decode() for text in corpus]
    corpus = [remove_extra_spaces(text) for text in corpus]
    corpus = strip_list_noempty(corpus)
    
    return corpus

import liwc
parse, category_names = liwc.load_token_parser('liwc.dic')

In [ ]:
corpus_fake = data_train[data_train.label == "fake"]["tweet"]
corpus_real = data_train[data_train.label == "real"]["tweet"]
corpus = data_train["tweet"]
corpus_fake = pre_processer_LIWC(corpus_fake)
print(corpus_fake)
corpus_real = pre_processer_LIWC(corpus_real)
print(corpus_real)
corpus = pre_processer(corpus)

In [34]:
import liwc
parse, category_names = liwc.load_token_parser('liwc.dic')

def LIWC(playlists):
    df = Counter(category for token in playlists for category in parse(token))
    return df

In [26]:
dfLIWC_topic1_fake = LIWC(playlists[0])
dfLIWC_topic2_fake = LIWC(playlists[1])
dfLIWC_topic3_fake = LIWC(playlists[2])
dfLIWC_topic4_fake = LIWC(playlists[3])
dfLIWC_topic5_fake = LIWC(playlists[4])
dfLIWC_topic6_fake = LIWC(playlists[5])
dfLIWC_topic7_fake = LIWC(playlists[6])
dfLIWC_topic8_fake = LIWC(playlists[7])

In [35]:
dfLIWC_topic1_real = LIWC(playlists_real[0])
dfLIWC_topic2_real = LIWC(playlists_real[1])
dfLIWC_topic3_real = LIWC(playlists_real[2])
dfLIWC_topic4_real = LIWC(playlists_real[3])
dfLIWC_topic5_real = LIWC(playlists_real[4])
dfLIWC_topic6_real = LIWC(playlists_real[5])
dfLIWC_topic7_real = LIWC(playlists_real[6])
dfLIWC_topic8_real = LIWC(playlists_real[7])
dfLIWC_topic9_real = LIWC(playlists_real[8])
dfLIWC_topic10_real = LIWC(playlists_real[9])
dfLIWC_topic11_real = LIWC(playlists_real[10])
dfLIWC_topic12_real = LIWC(playlists_real[11])
dfLIWC_topic13_real = LIWC(playlists_real[12])
dfLIWC_topic14_real = LIWC(playlists_real[13])
dfLIWC_topic15_real = LIWC(playlists_real[14])
dfLIWC_topic16_real = LIWC(playlists_real[15])
dfLIWC_topic17_real = LIWC(playlists_real[16])
dfLIWC_topic18_real = LIWC(playlists_real[17])
dfLIWC_topic19_real = LIWC(playlists_real[18])
dfLIWC_topic20_real = LIWC(playlists_real[19])
dfLIWC_topic21_real = LIWC(playlists_real[20])
dfLIWC_topic22_real = LIWC(playlists_real[21])
dfLIWC_topic23_real = LIWC(playlists_real[22])
dfLIWC_topic24_real = LIWC(playlists_real[23])
dfLIWC_topic25_real = LIWC(playlists_real[24])
dfLIWC_topic26_real = LIWC(playlists_real[25])
dfLIWC_topic27_real = LIWC(playlists_real[26])

In [36]:
dfLIWC_topic27_real

Counter({'affect': 8,
         'negemo': 6,
         'bio': 5,
         'health': 5,
         'posemo': 2,
         'cogmech': 3,
         'certain': 1,
         'space': 2,
         'relativ': 7,
         'anx': 1,
         'tentat': 1,
         'achieve': 3,
         'inhib': 1,
         'time': 4,
         'funct': 1,
         'number': 1,
         'motion': 1,
         'social': 1})

In [ ]:
#from collections import Counter
feature_counts = Counter(category for token in corpus_fake for category in parse(token))
print(feature_counts)

#### Real news

In [ ]:
#from collections import Counter
feature_counts = Counter(category for token in corpus_real for category in parse(token))
print(feature_counts)

#### All news

In [ ]:
#from collections import Counter
feature_counts = Counter(category for token in corpus for category in parse(token))
print(feature_counts)

## SentiNet

In [42]:
import nltk
from nltk.corpus import sentiwordnet as swn
nltk.download('averaged_perceptron_tagger')
nltk.download('wordnet')
nltk.download('sentiwordnet')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/rosalucassen/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/rosalucassen/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package sentiwordnet to
[nltk_data]     /Users/rosalucassen/nltk_data...
[nltk_data]   Unzipping corpora/sentiwordnet.zip.


True

In [75]:
def pre_processer_SENT(corpus):
    corpus = [remove_urls(text) for text in corpus]
    corpus = [remove_single_char(text) for text in corpus]
    corpus = [remove_numbers(text) for text in corpus]
    corpus = [remove_rt(text) for text in corpus]
    corpus = [remove_nonalpha(text) for text in corpus]
    corpus = [text.encode("ascii", "ignore") for text in corpus]
    corpus = [text.decode() for text in corpus]
    corpus = [remove_extra_spaces(text) for text in corpus]
    corpus = strip_list_noempty(corpus)
    
    processed_texts = [text for text in nlp.pipe(corpus, 
                                              disable=["ner",
                                                       "parser"])]
    tokenized_texts = [[word.lemma_ for word in lemma_ if not word.is_punct if not word.is_stop] 
                            for lemma_ in processed_texts]
    tokens = make_n_grams(tokenized_texts)
    return tokens

def penn_to_wn(tag):
    if tag.startswith('J'):
        return wn.ADJ
    elif tag.startswith('N'):
        return wn.NOUN
    elif tag.startswith('R'):
        return wn.ADV
    elif tag.startswith('V'):
        return wn.VERB
    return None

lemmatizer = nltk.WordNetLemmatizer()

def get_sentiment(word,tag):
    wn_tag = penn_to_wn(tag)
    if wn_tag not in (wn.NOUN, wn.ADJ, wn.ADV):
        return []

    lemma = lemmatizer.lemmatize(word, pos=wn_tag)
    if not lemma:
        return []

    synsets = wn.synsets(word, pos=wn_tag)
    if not synsets:
        return []

    synset = synsets[0]
    swn_synset = swn.senti_synset(synset.name())
    return [swn_synset.pos_score(),swn_synset.neg_score(),swn_synset.obj_score()]

data = data_train[data_train.label == "fake"]["tweet"]
data["text_n"] = data.str.replace('[^\w\s]',' ')
data['tokens']= data['text_n'].apply(pre_processer_SENT)

word_list=[]
for i in range(len(data['tokens'])):
    word_list.append([])

import numbers
for i in range(len(data['tokens'])): 
    for word in data['tokens'][i]:
        if word[:].isalpha():
            word_list[i].append(word[:])

tagged_tokens=[]
for token in word_list:
    tagged_tokens.append(nltk.pos_tag(token))
    
senti_val=[]
for i in range(len(tagged_tokens)):
    t=tuple(get_sentiment(x,y) for x,y in tagged_tokens[i])
    values= [x for x in t if x]
    senti_val.append(values)
data['value']=senti_val

calc=[]
#iterating over each sentence 
for i in range(len(senti_val)):
    # subtract positive and negative score of each token in the sentence 
    scores = [token_score[0] - token_score[1] for token_score in senti_val[i]]
    # if you want to sum up all the score within the sentence
    # scores = sum(scores) 
    print(scores)
    calc.append(scores)

AttributeError: 'list' object has no attribute 'isalpha'

In [83]:
playlists[1]

['Multiple Facebook posts claim Aussies fined found talking conspiracies [COVID-19]. posts included screenshot segment Australian breakfast television evidence claim.',
 'NYT invented video doctor fighting hospital.',
 'RT EllenCutch: Coronavirus misinformation moving offline. reddit user posted flyer site told delive',
 'Multiple posts shared thousands times Facebook Twitter YouTube claim salt effective remedy novel coronavirus.',
 "video shows Italian doctor says died Italy it's dangerous flu.",
 "Leaked Report Says 'Too Humans' Planet globalwarming conspiracy",
 'Video shows infected patient COVID-19 Dhanbad Hospital.',
 "photo funeral recently deceased Sri Lankan politician Arumugam Thondaman shared thousands times multiple Facebook posts. posts claim image shows Thondamans daughters violated Sri Lanka's mandatory quarantine policy travelers attending ceremony shortly returning country overseas.",
 'photo shows people infected lying sidewalk China.',
 'Man beaten Deoria India lockd

In [102]:
def pre_processer_SENT(corpus):
    corpus = [remove_urls(text) for text in corpus]
    corpus = [remove_single_char(text) for text in corpus]
    corpus = [remove_numbers(text) for text in corpus]
    corpus = [remove_rt(text) for text in corpus]
    corpus = [remove_nonalpha(text) for text in corpus]
    corpus = [text.encode("ascii", "ignore") for text in corpus]
    corpus = [text.decode() for text in corpus]
    corpus = [remove_extra_spaces(text) for text in corpus]
    corpus = strip_list_noempty(corpus)
    
    data = pd.DataFrame(corpus)
    data.columns = ["Tweet"]

    return data

In [107]:
data = pre_processer_SENT(playlists[1])

In [108]:
data

Tweet
0    Multiple Facebook posts claim Aussies fined found talking conspiracies [COVID-19]. posts included screenshot segment Australian breakfast television evidence claim.
1                                                                                                                            NYT invented video doctor fighting hospital.
2                                                                     RT EllenCutch: Coronavirus misinformation moving offline. reddit user posted flyer site told delive
3                                                           Multiple posts shared thousands times Facebook Twitter YouTube claim salt effective remedy novel coronavirus.
4                                                                                                          video shows Italian doctor says died Italy it's dangerous flu.
..                                                                                                                                                                    ...
588                                                                                                                      Boris Johnson shopping England time coronavirus.
589                                    video viewed thousands times multiple posts Facebook Twitter claim shows President Donald Trump tested positive novel coronavirus.
590                                                                          Central Park hospital tents housed thousands abused children released underground captivity.
591                                                                    men women clamped wooden plank claim people Thailand punished disobeying lockdown stepping houses.
592                                                                                                                . % deaths registered Italy COVID-19 died pathologies.

[593 rows x 1 columns]

In [109]:
# Getting nlp from spacy.load
#nlp=spacy.load('en')
# Making the function to get the sentiments out of the dataframe
def get_sentiment(data, name):
    count=1
    l=len(data)
    positive_sentiments=[]
    negative_sentiments=[]
    for tex in data[name]:
        print('The current status is :',count*100/l,'%')
        tex=nlp(tex)
        noun=[]
        verb=[]
        adj=[]
        adv=[]
        for i in tex :
            if i.pos_=='NOUN':
                noun.append(i)
            elif i.pos_ =='ADJ':
                adj.append(i)
            elif i.pos_ =='VERB':
                verb.append(i)
            elif i.pos_=='ADV':
                adv.append(i)
        clear_output(wait=True)
        count+=1
        neg_score=[]
        pos_score=[]
        for i in tex :
            try:
                if i in noun:
                    x=swn.senti_synset(str(i)+'.n.01')
                    neg_score.append(x.neg_score())
                    pos_score.append(x.pos_score())
                elif i in adj:
                    x=swn.senti_synset(str(i)+'.a.02')
                    neg_score.append(x.neg_score())
                    pos_score.append(x.pos_score())
                elif i in adv :
                    x=swn.senti_synset(str(i)+'.r.02')
                    neg_score.append(x.neg_score())
                    pos_score.append(x.pos_score())
                elif i in verb :
                    x=swn.senti_synset(str(i)+'.v.02')
                    neg_score.append(x.neg_score())
                    pos_score.append(x.pos_score())

            except:
                pass
        positive_sentiments.append(np.mean(pos_score))
        negative_sentiments.append(np.mean(neg_score))

    data['Positive Sentiment']=positive_sentiments
    data['Negative Sentiment']=negative_sentiments

In [110]:
from IPython.display import clear_output

import seaborn as sns
import matplotlib.pyplot as plt
from wordcloud import WordCloud

get_sentiment(data, "Tweet")

The current status is : 100.0 %


In [113]:
overall=[]
for i in range(len(data)):
    if data['Positive Sentiment'][i]>data['Negative Sentiment'][i]:
        overall.append('Positive')
    elif data['Positive Sentiment'][i]<data['Negative Sentiment'][i]:
        overall.append('Negative')
    else:
        overall.append('Neutral')
data['Overall Sentiment']=overall

In [112]:
data.head()

Tweet  \
0  Multiple Facebook posts claim Aussies fined found talking conspiracies [COVID-19]. posts included screenshot segment Australian breakfast television evidence claim.   
1                                                                                                                          NYT invented video doctor fighting hospital.   
2                                                                   RT EllenCutch: Coronavirus misinformation moving offline. reddit user posted flyer site told delive   
3                                                         Multiple posts shared thousands times Facebook Twitter YouTube claim salt effective remedy novel coronavirus.   
4                                                                                                        video shows Italian doctor says died Italy it's dangerous flu.   

   Positive Sentiment  Negative Sentiment Overall Sentiment  
0            0.017857            0.000000          Positive  
1            0.083333            0.000000          Positive  
2            0.031250            0.093750          Negative  
3            0.208333            0.020833          Positive  
4            0.156250            0.187500          Negative